<center><h1>M1 MMA - Optimisation</h1><h2>TP3 : descente de gradient par rebroussement d'Armijo</h2></center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from time import time
params = {'tex.usetex': True}

<h2>I - Application à un problème de classification</h2>

In [ ]:
# Paramètres pour générer les données du problème.
t = 2*np.pi*np.random.rand()
u = np.array([np.cos(t), np.sin(t)])
#

On considère donnée une famille de couples $((x_i,y_i))_{0\leq i\leq M-1}$ où pour tout $i$, $x_i$ est un point du plan $\mathbb{R}^2$ et $y_i\in\{-1,1\}$ défini l'appartenance de $x_i$ à une des deux classes représentées par les nombres $-1$ et $1$.

Les couples $((x_i,y_i))_{0\leq i\leq M-1}$ sont une réalisation d'un échantillon de taille $M$ de la variable aléatoire $(X,Y)$ à valeurs dans $\mathbb{R}^2\times\{-1,1\}$, c'est-à-dire une réalisation de $M$ variables aléatoires indépendantes $(X_i,Y_i)$ de même loi que le couple $(X,Y)$.

Une réalisation de la variable $(X,Y)$ est donnée par la fonction $\mbox{genererCouple}$ suivante :

In [ ]:
def genererCouple():
    # renvoie une réalisation de la variable aléatoire (X,Y)
    if np.random.rand() < 0.5:
        x, y = 2.*np.random.randn(2) + 3*u, -1 # bleu
    else:
        x, y = 2.*np.random.randn(2) - 3*u, 1 # rouge
    return [x, y]

La cellule suivante génère les données du problème $((x_i,y_i))_{0\leq i\leq M-1}$ et les affiche graphiquement. La population de type "-1" (c'est-à-dire les $x_i$ tels que $y_i=-1$) est affichée en vert et celle de type "1" en rouge. Les $x_i$ sont stockés dans un vecteur $\mbox{xi_list}$ et les $y_i$ dans un vecteur $\mbox{yi_list}$.

In [ ]:
# génération des données
M = 1000
xi_list, yi_list = np.zeros((M, 2)), np.zeros(M)
for i in range(M):
    xi_list[i, :], yi_list[i] = genererCouple() # on stocke les données ((x_i, y_i))_i

# affichage
plt.figure(figsize = (6, 6))
for i in range(M):
    if yi_list[i] == 1: # si x_i est de classe 1 alors on affiche un point rouge
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "red")
    else: # sinon x_i est de classe -1 alors on affiche un point vert
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "green")
plt.title(u"Représentation des données.\n" + r"$x_i$ est un point vert si $y_i = -1$, point rouge si $y_i = 1$.")
plt.axis("tight")
plt.show()

L'objectif de ce TP est, à partir des données d'entraînement ci-dessus $((x_i,y_i))_{0\leq i\leq M-1}$, d'apprendre à prédire, sachant une nouvelle réalisation $x\in\mathbb{R}^2$ de $X$, la classe de $x$ associée.

Pour cela on va déterminer la meilleure droite passant par $(0,0)$ qui sépare les deux classes ou populations (vert et rouge / $-1$ et $1$) des données.

Une droite qui passe par $(0,0)$ a pour équation $f_a(x) = 0$ où $f_a : x\in\mathbb{R}^2 \mapsto a_0 x_0 + a_1 x_1$ avec $a = (a_0, a_1)\in\mathbb{R}^2$ un vecteur normal de la droite.

L'idée est donc de trouver la meilleure orientation (paramétrée par $a\in\mathbb{R}^2$) d'une droite de sorte qu'une nouvelle réalisation $x$ de $X$ satisfaisant $f_a(x) > 0$ serait associé à la classe $y=1$ et $f_a(x) < 0$ serait associé à la classe $y = -1$.

Pour déterminer cette meilleure orientation $a\in\mathbb{R}^2$, nous allons chercher à résoudre le problème d'optimisation suivant : 
$$
    \min_{a\in\mathbb{R}^2} \ F(a), \quad \mbox{ où } F:a\in\mathbb{R}^2\mapsto \lambda \|a\|_2^2 + \frac1M \sum_{i=0}^{M-1} \log(1 + e^{-y_i (a_0 x_{i,0} + a_1 x_{i,1})}),
$$
où $\lambda > 0$ est un paramètre fixé et les $x_i = (x_{i,0}, x_{i,1})\in\mathbb{R}^2$ et $y_i\in\{-1,1\}$ sont les données du problème. Ici $\log$ représente le logarithme népérien.

<h3>Résolution numérique du problème d'optimisation</h3>

L'implémentation de $F$ est donnée ci-dessous.

On définit $\mbox{y_a}$ comme le résultat du produit matriciel entre $\mbox{xi_list}$ et $a$.
Ainsi le signe des coefficients de $\mbox{y_a}$ donne la classe des points $x_i$ prédites par la droite de vecteur normal $a$.

In [ ]:
λ = 0.05
def F(a):
    # implémentation vectorialisée du calcul des quantités <xi, a> pour i \in {0,...,M-1}
    y_a = np.dot(xi_list, a)

    L = np.log(1 + np.exp(-yi_list*y_a))
    return λ*np.dot(a, a) + 1/M*np.sum(L)

<b>1) Calculer le gradient de $F$ en $a\in\mathbb{R}^2$. On pourra introduire la fonction $g :t\in\mathbb{R}\mapsto\log(1+e^{-t})$</b>

On a pour tout $a\in\mathbb R^2$, $\nabla F(a) = 2\lambda a + \frac1M\sum_{i=0}^{M-1} g'(y_i\langle x_i, a \rangle) y_i x_i$, où $g:t\in\mathbb{R}\mapsto \log(1+e^{-t})$.

On a pour tout $t\in\mathbb{R}$, $g'(t) = -\frac{e^{-t}}{1+e^{-t}}$.

<b>2) Montrer que le problème d'optimisation admet une unique solution sur $\mathbb{R}^2$.</b>

<b>3) Ecrire en Python une fonction $\mbox{gradF}$ prenant en argument $a\in\mathbb{R}^2$ et renvoyant $\nabla F(a)$.</b>

In [ ]:
# Valider cette case pour vérifier que votre implémentation du gradient de F est correcte
a = np.random.rand(2)
epsilon = 1e-8
print("Cette quantité doit être inférieure à 1e-6 : ", np.linalg.norm(gradF(a) - np.array([(F(a + epsilon*np.array([1,0])) - F(a))/(epsilon), (F(a + epsilon*np.array([0,1])) - F(a))/(epsilon)])))

<b>4) Ecrire en Python une fonction $\mbox{descente_gradient_rebroussement}$ prenant en argument la fonction objectif $f$, son gradient $\mbox{gradf}$, $\mbox{x0}$ (un point de départ), $\alpha$ et $\beta$ (pour la méthode du rebroussement d'Armijo), $\mbox{epsilon}$ (une tolérance), et $\mbox{Niter}$ (un nombre d'itérations maximum); implémentant l'algorithme de la descente de gradient par rebroussement d'Armijo. La fonction renverra la valeur du dernier itéré ainsi que la liste des itérés successifs. On fera attention à évaluer les fonctions $f$ et $\mbox{gradf}$ le moins de fois possible.

On pourra éventuellement implémenter à part une fonction codant la méthode du calcul d'un pas de descente par rebroussement d'Armijo.</b>

<b>5) Illustrer la converge de l'algorithme en utilisant la fonction $\mbox{plt.semilogy}$. (Indication : on utilisera d'abord l'algorithme avec une tolérance faible, par exemple $10^{-8}$, et on utilisera l'approximée obtenu comme limite de référence).</b>

<b>6) De quel type de convergence s'agit-il ? Justifier.</b>

<b>7) Vérifier la trajectoire obtenue via l'algorithme de descente avec les lignes de niveau de $F$.</b>

In [ ]:
# Definition des grilles et evaluation de f
a_list_0 = [a_list[i][0] for i in range(len(a_list))] # on recupère les abscisses des itérés
a_list_1 = [a_list[i][1] for i in range(len(a_list))] # on recupère les ordonnées des itérés
a_0_min, a_0_max = np.min(a_list_0) - .25, np.max(a_list_0) + .25 # on définit les bornes des abscisses pour le graphe
a_1_min, a_1_max = np.min(a_list_1) - .25, np.max(a_list_1) + .25 # on définit les bornes des ordonnées pour le graphe
s = 100
a_0 = np.linspace(a_0_min, a_0_max, s) # grille abscisses
a_1 = np.linspace(a_1_min, a_1_max, s) # grille ordonnées
a_0, a_1 = np.meshgrid(a_0, a_1) # grille abcisses, grille ordonnées -> grille 2D
Z = np.zeros((s, s))
for i in range(s):
    for j in range(s):
        Z[i, j] = F([a_0[i, j], a_1[i, j]]) # valeurs de F sur la grille 2D

# Graphique des lignes de niveaux
fig, ax = plt.subplots(figsize = (6, 6))
CS = ax.contour(a_0, a_1, Z, 25)

plt.plot(a_list_0, a_list_1, marker = "o", ms = 4.0, color = "red")
plt.plot(a_star[0], a_star[1], marker = '*', ms = 15.0, color = "r")
ax.clabel(CS, fontsize = 8)
ax.set_title('Lignes de niveau')
ax.set_aspect('equal', adjustable = 'box')

<b>8) On considère la fonction $\mbox{f}$ suivante, où $\mbox{a_star}$ représente l'approximation de la solution renvoyée par l'algorithme.</b>

In [ ]:
def sigmoid(t):
    return 2/(1 + np.exp(-2*t)) - 1

In [ ]:
def prediction(x):
    return sigmoid(x[0]*a_star[0] + x[1]*a_star[1])

In [ ]:
tt = np.linspace(-10, 10, 200)
plt.plot(tt, sigmoid(tt))
plt.title("Fonction sigmoïde")
plt.show()

<b>Interpréter la figure suivante.</b>

In [ ]:
X0 = np.linspace(-11, 11, 100)
X1 = np.linspace(-11, 11, 100)
X0, X1 = np.meshgrid(X0, X1)
Z = f([X0, X1])

# Graphique des lignes de niveaux
fig, ax = plt.subplots(figsize = (6, 6))
CS = ax.contourf(X0, X1, Z, 50, cmap = "copper")
for i in range(M):
    if yi_list[i] == 1:
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "red")
    else:
        plt.plot(xi_list[i, 0], xi_list[i, 1], linestyle = "none", marker = '.', color = "blue")
ax.clabel(CS, fontsize = 8)
ax.set_title(r"Séparation des observations $x_i$ en leurs label $y_i$ par $f$")
ax.set_aspect("equal", adjustable = "box") # pour que les axes aient la même échelle

Représentation de la distribution des points $x_i$ avec leurs classes $\pm1$. La colormap en fond représente la fonction prédictrice $f$ construite à partir de la solution approchée trouvée $\mbox{a_star}$ du problème d'optimisation $\min_{a\in\mathbb{R}^2} F(a)$.

<h3>II) Application au débruitage d'images</h3>

In [ ]:
def ps(x, y):
    # produit scalaire entre x et y, qui peuvent être des vecteurs ou des matrices.
    return np.sum(x*y)

Récupérer l'image à l'adresse : https://qdenoyelle.github.io/M1_Optim/TP/hameau.png et la placer dans le dossier où le TP se situe.

In [ ]:
plt.figure(figsize = (8, 6))
img_original = plt.imread("hameau.png").astype(float) # chargement de l'image
img_original = sum([img_original[:, :, i] for i in range(2)]) # on transforme l'image en noir et blanc
img_original = 1/(np.max(img_original)-np.min(img_original))*(img_original - np.min(img_original))
plt.imshow(img_original, cmap = 'gray') # affichage de l'image
plt.show()

On va traiter l'image comme une matrice dont les coefficients sont le niveau de gris des pixels.

In [ ]:
n, m = img_original.shape # on récupère le nombre de ligne et de colonnes.
print("Nombre de lignes : ", n)
print("Nombre de colonnes : ", m)

On va maintenant dégrader l'image par un bruit additif gaussien (en pratique on aurait uniquement accès à l'image bruitée, ici on cré "artificiellement" le bruit).

In [ ]:
bruit = .2 * np.random.randn(n, m) # bruit gaussien qui va être appliqué sur l'image
img_bruit = img_original + bruit # on bruite additivement l'image

<b>1) Afficher l'image bruitée.</b>

In [ ]:
plt.figure(figsize = (8, 6))
plt.imshow(img_bruit, cmap = "gray") # affichage de l'image
plt.show()

In [ ]:
y = img_bruit # on stocke dans y l'image bruitée 

Dans la suite les images seront vues comme des tableaux de valeurs (chaque pixel est un nombre représentant le niveau de gris), c'est à dire des matrices à $n$ lignes et $m$ colonnes.

On va maintenant chercher à débruiter l'image ci-dessus (i.e. diminuer l'impact du bruit). La méthode adoptée va consister à résoudre le problème d'optimisation suivant
$$
\min_{x\in\mathcal{M}_{n,m}(\mathbb{R})} F(x),
$$
où
$$
F(x) = \frac12 \sum_{i=1}^n\sum_{j=1}^m (x_{i,j} - y_{i,j})^2 + \lambda \sum_{i=1}^{n-1}\sum_{j=1}^m N_\varepsilon(x_{i+1,j} - x_{i,j}) + \lambda \sum_{i=1}^{n}\sum_{j=1}^{m-1} N_\varepsilon(x_{i,j+1} - x_{i,j}).
$$
$y\in\mathcal{M}_{n,m}(\mathbb{R})$ est l'image bruitée (la donnée du problème), $\lambda>0$ une constante et 
$$
\forall t\in\mathbb R, \quad N_\varepsilon(t) = \sqrt{t^2+\varepsilon},
$$
avec $\varepsilon>0$.

<b>3) Interpréter $F$.</b>

<b>4) Justifier que $F$ est $\mathcal C^\infty$ sur $\mathcal{M}_{n,m}(\mathbb{R})$. Montrer que $F$ est strictement convexe et admet un unique minimum global sur $\mathcal{M}_{n,m}(\mathbb{R})$.</b>

<b>5) Voici ci-dessous une implémentation vectorialisée de $F$ et de son gradient de $F$. Les matrices $L\in\mathcal{M}_{n-1, n}(\mathbb{R})$ avec des $-1$ sur la diagonale, et des $1$ sur la sur-diagonale, et $C\in\mathcal{M}_{m, m-1}(\mathbb{R})$ la matrice avec des $-1$ sur la diagonale, $1$ sur la sous-diagonale ont été introduites</b>.

In [ ]:
L = np.zeros([n - 1, n])
for i in range(n - 1):
    for j in range(n):
        if i == j:
            L[i, j] = -1
        if j == i + 1:
            L[i, j] = 1

C = np.zeros([m, m - 1])
for i in range(m):
    for j in range(m - 1):
        if i == j:
            C[i, j] = -1
        if i == j + 1:
            C[i, j] = 1

In [ ]:
# En première lecture, vous pouvez vous concentrer sur les implémentations des fonctions données
# dans les "else".
#
# Elles correspondent à des implémentations "naïves" et directes des opérations demandées.
# Nous verrons plus tard qu'il est possible de réécrire ces opérations de manière plus efficace.
#
# Le booléen "implementation_efficace", que l'on fixera comme vrai ou faux à la demande, permettra
# de switcher entre l'une ou l'autre des implémentations pour tester la différence de vitesse d'éxécution.


implementation_efficace = True

def Lp(x):
    if implementation_efficace:
        return x[1:n, :] - x[0:n-1, :]
    else:
        return np.dot(L, x)
def Lt(v):
    if implementation_efficacelow_complexity_implementation:
        u = np.zeros([n , m])
        u[0, :] = -v[0, :]
        u[1:n-1, :] = v[0:n-2, :] - v[1:n-1, :]
        u[n-1, :] = v[n-2, :]
        return u
    else:
        return np.dot(L.transpose(), v)
def Cp(x):
    if implementation_efficace:
        return x[:, 1:m] - x[:, 0:m-1]
    else:
        return np.dot(x, C)
def Ct(v):
    if implementation_efficacelow_complexity_implementation:
        u = np.zeros([n , m])
        u[:, 0] = -v[:, 0]
        u[:, 1:m-1] = v[:, 0:m-2] - v[:, 1:m-1]
        u[:, m-1] = v[:, m-2]
        return u
    else:
        return np.dot(v, C.transpose())

epsilon = 1e-5
def N_eps(t):
    return np.sqrt(t**2 + epsilon)
def dN_eps(t):
    return t/N_eps(t)
def R(x):
    return np.sum(N_eps(Lp(x))) + np.sum(N_eps(Cp(x)))

In [ ]:
# Implémentation fonction objectif
def F(x):
    return .5*ps(x - y, x - y) + lbda*R(x)

In [ ]:
def gradR(x):
    return Lt(dN_eps(Lp(x))) + Ct(dN_eps(Cp(x)))

# implémentation gradient de F
def gradF(x):
    return x - y + lbda*gradR(x)

<b>6) Utiliser l'algorithme de descente de gradient par rebroussement d'Armijo pour le résoudre le problème d'optimisation. On prendra pour l'instant $\lambda = 0.3$.</b>

In [ ]:
lbda = .3
alpha, beta = 1e-4, .2 # valeurs de alpha et beta qui donne une convergence relativement rapide de l'algorithme.
# Faites vos tests !





<b>7) Illustrer la convergence de l'algorithme.</b>

<b>8) Afficher l'image reconstruite et la comparée aux autres images. Commenter.</b>

<b>9) On considère la fonction $\mbox{snr}$ suivante qui donne une mesure de la qualité de la reconstruction (plus $\mbox{snr}(x)$ est grand, mieux c'est). Trouver une valeur de $\lambda$ qui donne une reconstruction proche de l'optimal pour cette métrique de performance.</b>

In [ ]:
def snr(x):
    # fonction "Signal to Noise ratio"
    return -10*np.log(ps(x - img_original, x - img_original)/ps(x, x))/np.log(10)